# Notebook for replicating the analyses in "The Effect of Increasing the Idaho Child Tax Credit"
### Richard W. Evans and Sydney Beutler, April 2024
This notebook replicates the analyses by [Richard W. Evans](https://sites.google.com/site/rickecon) and Sydney Beutler entitled "The Effect of Increasing the Idaho Child Tax Credit".

This Jupyter notebook is meant for execution on your local machine and is located at https://github.com/TheCGO/ID-CTC/blob/main/ID_CTC.ipynb.

## 0. Setting up the environment
To set up the environment:
1. Update your local clone of the `fiscalsim-us` repository on your machine
    * If you don't have the `fiscalsim-us` repository cloned on your machine:
        * Create a fork of the FiscalSim-US main repository (https://github.com/TheCGO/fiscalsim-us) to your GitHub account
        * Navigate to the directory in your terminal where you want to save this repository
        * Clone that fork onto your local machine: `git clone https://github.com/[YourGitHubHandle]/fiscalsim-us.git`
        * Change directory to the new `fiscalsim-us` directory: `cd fiscalsim-us`
        * Create an `upstream` remote that points to the main repository: `git remote add upstream https://github.com/thecgo/fiscalsim-us.git`
    * If you already have the `fiscalsim-us` repository cloned on your machine:
        * Navigate to your `fiscalsim-us` repository directory in your terminal.
        * Make sure you have an `upstream` remote that points to the main `fiscalsim-us` directory
        * Make sure your main branch is updated with the most current changes in the fiscalsim-us `main` directory: `git fetch upstream`
        * Merge those changes into your `main` directory: `git merge upstream/main`
        * Push those changes out to your remote fork: `git push origin main`
2. Create a new branch called `rickecon-pe06220` that comes from Rick's `pe06220` branch
    * Create a new branch called `rickecon-pe06220`: `git checkout -b rickecon-pe06220 main`
    * Pull the changes from Rick's branch into this new branch of your local fork: `git pull https://github.com/rickecon/fiscalsim-us.git pe06220`
3. Create a new conda environment from this `rickecon-pe06220` branch called `fiscalsim-us-dev2`
    * Navigate to the `fiscalsim-us` repository directory in your terminal on your local machine
    * Create the base of the conda environment using the `environment.yml` file in this repository: `conda env create -f environment.yml`
    * Activate the new conda environment: `conda activate fiscalsim-us-dev2`
    * Install fiscalsim-us package directly from this repository's `setup.py` file.
        * For Linux: `pip install -e .[dev]`
        * For Mac: `pip install -e ."[dev]"`
        * For Windows: `pip install -e .'[dev]'`

In your new branch `rickecon-pe06220`, with the new conda environment `fiscalsim-us-dev2` activated, you should be able to run all the analyses below.

### 1. Introduction
Before opening and running this notebook, make sure that you have downloaded or cloned the ID-CTC repository (https://github.com/TheCGO/ID-CTC) and created and activated the associated conda environment `id-ctc-dev` in the `environment.yml` file.

The notebook for the introduction produces the following figures.

* 1.1. Figure 1. Plot of US states by state type of state CTC

In [1]:
# Import packages (this might take a little more than a minute)
import pandas as pd
import numpy as np
import geopandas as gpd
from bokeh.io import output_file, output_notebook, export_png
from bokeh.plotting import figure, show
from bokeh.models import (ColumnDataSource, Title, Label, LabelSet, Legend,
                          LegendItem, CategoricalColorMapper, ColorBar,
                          HoverTool, NumeralTickFormatter, GeoJSONDataSource,
                          FactorRange)
from bokeh.models.tickers import SingleIntervalTicker
from bokeh.transform import factor_cmap
from bokeh.sampledata.us_states import data as states
from bokeh.palettes import Category10

import random
import json

from fiscalsim_us.model_api import *
from fiscalsim_us import Simulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant

### 1.1. Figure 1. Plot of US states by state employment income tax type

Create the data for state tax type

In [2]:
# Create a DataFrame of states and their child tax credit types as of
# January 1, 2024. See the following 2022 ITEP report.
# https://itep.org/state-child-tax-credits-and-child-poverty-50-state-analysis/
# 0 = No state CTC
# 1 = Refundable state CTC
# 2 = Nonrefundable state CTC
# 3 = One-time or temporary CTC
state_taxtype_list = [
    ["Alabama", "AL", 2],
    ["Alaska", "AK", 0],
    ["Arizona", "AZ", 1],
    ["Arkansas", "AR", 2],
    ["California", "CA", 3],
    ["Colorado", "CO", 1],
    ["Connecticut", "CT", 3],
    ["Delaware", "DE", 3],
    ["District of Columbia", "DC", 3],
    ["Florida", "FL", 0],
    ["Georgia", "GA", 1],
    ["Hawaii", "HI", 3],
    ["Idaho", "ID", 1],
    ["Illinois", "IL", 1],
    ["Indiana", "IN", 1],
    ["Iowa", "IA", 2],
    ["Kansas", "KS", 3],
    ["Kentucky", "KY", 1],
    ["Louisiana", "LA", 3],
    ["Maine", "ME", 3],
    ["Maryland", "MD", 3],
    ["Massachusetts", "MA", 1],
    ["Michigan", "MI", 1],
    ["Minnesota", "MN", 3],
    ["Mississippi", "MS", 1],
    ["Missouri", "MO", 2],
    ["Montana", "MT", 2],
    ["Nebraska", "NE", 3],
    ["Nevada", "NV", 0],
    ["New Hampshire", "NH", 0],
    ["New Jersey", "NJ", 3],
    ["New Mexico", "NM", 3],
    ["New York", "NY", 3],
    ["North Carolina", "NC", 1],
    ["North Dakota", "ND", 3],
    ["Ohio", "OH", 3],
    ["Oklahoma", "OK", 2],
    ["Oregon", "OR", 3],
    ["Pennsylvania", "PA", 1],
    ["Rhode Island", "RI", 3],
    ["South Carolina", "SC", 3],
    ["South Dakota", "SD", 0],
    ["Tennessee", "TN", 0],
    ["Texas", "TX", 0],
    ["Utah", "UT", 1],
    ["Virginia", "VA", 3],
    ["Vermont", "VT", 3],
    ["Washington", "WA", 0],
    ["West Virginia", "WV", 3],
    ["Wisconsin", "WI", 3],
    ["Wyoming", "WY", 0],
]
state_taxtype_df = pd.DataFrame(
    state_taxtype_list, columns=["State", "Abbrev", "TaxType"]
)
state_taxtype_df["TaxType_str"] = ""
state_taxtype_df["TaxType_str"][state_taxtype_df["TaxType"]==0] = \
    "No state labor income tax"
state_taxtype_df["TaxType_str"][state_taxtype_df["TaxType"]==1] = \
    "Flat state income tax rate"
state_taxtype_df["TaxType_str"][state_taxtype_df["TaxType"]==2] = \
    "Nearly flat state income tax rates"
state_taxtype_df["TaxType_str"][state_taxtype_df["TaxType"]==3] = \
    "Progressive state income tax rates"
state_taxtype_df["TaxType_str_short"] = ""
state_taxtype_df["TaxType_str_short"][state_taxtype_df["TaxType"]==0] = \
    "No income tax"
state_taxtype_df["TaxType_str_short"][state_taxtype_df["TaxType"]==1] = \
    "Flat income tax rate"
state_taxtype_df["TaxType_str_short"][state_taxtype_df["TaxType"]==2] = \
    "Nearly flat income tax rates"
state_taxtype_df["TaxType_str_short"][state_taxtype_df["TaxType"]==3] = \
    "Progressive income tax rates"
state_taxtype_df["fill_color"] = ""
state_taxtype_df["fill_color"][state_taxtype_df["TaxType"]==0] = "#D8D3D3"
state_taxtype_df["fill_color"][state_taxtype_df["TaxType"]==1] = "red"
state_taxtype_df["fill_color"][state_taxtype_df["TaxType"]==2] = "purple"
state_taxtype_df["fill_color"][state_taxtype_df["TaxType"]==3] = "blue"

# Sort alphabetically by full state name
state_taxtype_df.sort_values("State", inplace=True, ignore_index=True)

# Create sub-DataFrames for each tax type
no_tax_states_df = \
    state_taxtype_df[state_taxtype_df["TaxType"]==0].reset_index(drop=True)
flat_tax_states_df = \
    state_taxtype_df[state_taxtype_df["TaxType"]==1].reset_index(drop=True)
nflat_tax_states_df = \
    state_taxtype_df[state_taxtype_df["TaxType"]==2].reset_index(drop=True)
prog_tax_states_df = \
    state_taxtype_df[state_taxtype_df["TaxType"]==3].reset_index(drop=True)
print(state_taxtype_df.groupby("TaxType").count())

# Save state_data_df as .csv
state_taxtype_df.to_csv('./data/state_taxtype.csv', index=False)
state_taxtype_df

         State  Abbrev  TaxType_str  TaxType_str_short  fill_color
TaxType                                                           
0            9       9            9                  9           9
1           13      13           13                 13          13
2            6       6            6                  6           6
3           23      23           23                 23          23


State Abbrev  TaxType                         TaxType_str  \
0                Alabama     AL        2  Nearly flat state income tax rates   
1                 Alaska     AK        0           No state labor income tax   
2                Arizona     AZ        1          Flat state income tax rate   
3               Arkansas     AR        2  Nearly flat state income tax rates   
4             California     CA        3  Progressive state income tax rates   
5               Colorado     CO        1          Flat state income tax rate   
6            Connecticut     CT        3  Progressive state income tax rates   
7               Delaware     DE        3  Progressive state income tax rates   
8   District of Columbia     DC        3  Progressive state income tax rates   
9                Florida     FL        0           No state labor income tax   
10               Georgia     GA        1          Flat state income tax rate   
11                Hawaii     HI        3  Progressive state income tax rates   
12                 Idaho     ID        1          Flat state income tax rate   
13              Illinois     IL        1          Flat state income tax rate   
14               Indiana     IN        1          Flat state income tax rate   
15                  Iowa     IA        2  Nearly flat state income tax rates   
16                Kansas     KS        3  Progressive state income tax rates   
17              Kentucky     KY        1          Flat state income tax rate   
18             Louisiana     LA        3  Progressive state income tax rates   
19                 Maine     ME        3  Progressive state income tax rates   
20              Maryland     MD        3  Progressive state income tax rates   
21         Massachusetts     MA        1          Flat state income tax rate   
22              Michigan     MI        1          Flat state income tax rate   
23             Minnesota     MN        3  Progressive state income tax rates   
24           Mississippi     MS        1          Flat state income tax rate   
25              Missouri     MO        2  Nearly flat state income tax rates   
26               Montana     MT        2  Nearly flat state income tax rates   
27              Nebraska     NE        3  Progressive state income tax rates   
28                Nevada     NV        0           No state labor income tax   
29         New Hampshire     NH        0           No state labor income tax   
30            New Jersey     NJ        3  Progressive state income tax rates   
31            New Mexico     NM        3  Progressive state income tax rates   
32              New York     NY        3  Progressive state income tax rates   
33        North Carolina     NC        1          Flat state income tax rate   
34          North Dakota     ND        3  Progressive state income tax rates   
35                  Ohio     OH        3  Progressive state income tax rates   
36              Oklahoma     OK        2  Nearly flat state income tax rates   
37                Oregon     OR        3  Progressive state income tax rates   
38          Pennsylvania     PA        1          Flat state income tax rate   
39          Rhode Island     RI        3  Progressive state income tax rates   
40        South Carolina     SC        3  Progressive state income tax rates   
41          South Dakota     SD        0           No state labor income tax   
42             Tennessee     TN        0           No state labor income tax   
43                 Texas     TX        0           No state labor income tax   
44                  Utah     UT        1          Flat state income tax rate   
45               Vermont     VT        3  Progressive state income tax rates   
46              Virginia     VA        3  Progressive state income tax rates   
47            Washington     WA        0           No state labor income tax   
48         West Virginia     WV        3  Progressive state income tax rates   
49             Wisc

In [3]:
# Print the no tax states
no_tax_states_df

State Abbrev  TaxType                TaxType_str TaxType_str_short  \
0         Alaska     AK        0  No state labor income tax     No income tax   
1        Florida     FL        0  No state labor income tax     No income tax   
2         Nevada     NV        0  No state labor income tax     No income tax   
3  New Hampshire     NH        0  No state labor income tax     No income tax   
4   South Dakota     SD        0  No state labor income tax     No income tax   
5      Tennessee     TN        0  No state labor income tax     No income tax   
6          Texas     TX        0  No state labor income tax     No income tax   
7     Washington     WA        0  No state labor income tax     No income tax   
8        Wyoming     WY        0  No state labor income tax     No income tax   

  fill_color  
0    #D8D3D3  
1    #D8D3D3  
2    #D8D3D3  
3    #D8D3D3  
4    #D8D3D3  
5    #D8D3D3  
6    #D8D3D3  
7    #D8D3D3  
8    #D8D3D3

In [4]:
# Print the flat tax states
flat_tax_states_df

State Abbrev  TaxType                 TaxType_str  \
0          Arizona     AZ        1  Flat state income tax rate   
1         Colorado     CO        1  Flat state income tax rate   
2          Georgia     GA        1  Flat state income tax rate   
3            Idaho     ID        1  Flat state income tax rate   
4         Illinois     IL        1  Flat state income tax rate   
5          Indiana     IN        1  Flat state income tax rate   
6         Kentucky     KY        1  Flat state income tax rate   
7    Massachusetts     MA        1  Flat state income tax rate   
8         Michigan     MI        1  Flat state income tax rate   
9      Mississippi     MS        1  Flat state income tax rate   
10  North Carolina     NC        1  Flat state income tax rate   
11    Pennsylvania     PA        1  Flat state income tax rate   
12            Utah     UT        1  Flat state income tax rate   

       TaxType_str_short fill_color  
0   Flat income tax rate        red  
1   Flat income tax rate        red  
2   Flat income tax rate        red  
3   Flat income tax rate        red  
4   Flat income tax rate        red  
5   Flat income tax rate        red  
6   Flat income tax rate        red  
7   Flat income tax rate        red  
8   Flat income tax rate        red  
9   Flat income tax rate        red  
10  Flat income tax rate        red  
11  Flat income tax rate        red  
12  Flat income tax rate        red

In [5]:
# Print the nearly flat tax states
nflat_tax_states_df

State Abbrev  TaxType                         TaxType_str  \
0   Alabama     AL        2  Nearly flat state income tax rates   
1  Arkansas     AR        2  Nearly flat state income tax rates   
2      Iowa     IA        2  Nearly flat state income tax rates   
3  Missouri     MO        2  Nearly flat state income tax rates   
4   Montana     MT        2  Nearly flat state income tax rates   
5  Oklahoma     OK        2  Nearly flat state income tax rates   

              TaxType_str_short fill_color  
0  Nearly flat income tax rates     purple  
1  Nearly flat income tax rates     purple  
2  Nearly flat income tax rates     purple  
3  Nearly flat income tax rates     purple  
4  Nearly flat income tax rates     purple  
5  Nearly flat income tax rates     purple

In [6]:
# Print the progressive tax states
prog_tax_states_df

State Abbrev  TaxType                         TaxType_str  \
0             California     CA        3  Progressive state income tax rates   
1            Connecticut     CT        3  Progressive state income tax rates   
2               Delaware     DE        3  Progressive state income tax rates   
3   District of Columbia     DC        3  Progressive state income tax rates   
4                 Hawaii     HI        3  Progressive state income tax rates   
5                 Kansas     KS        3  Progressive state income tax rates   
6              Louisiana     LA        3  Progressive state income tax rates   
7                  Maine     ME        3  Progressive state income tax rates   
8               Maryland     MD        3  Progressive state income tax rates   
9              Minnesota     MN        3  Progressive state income tax rates   
10              Nebraska     NE        3  Progressive state income tax rates   
11            New Jersey     NJ        3  Progressive state income tax rates   
12            New Mexico     NM        3  Progressive state income tax rates   
13              New York     NY        3  Progressive state income tax rates   
14          North Dakota     ND        3  Progressive state income tax rates   
15                  Ohio     OH        3  Progressive state income tax rates   
16                Oregon     OR        3  Progressive state income tax rates   
17          Rhode Island     RI        3  Progressive state income tax rates   
18        South Carolina     SC        3  Progressive state income tax rates   
19               Vermont     VT        3  Progressive state income tax rates   
20              Virginia     VA        3  Progressive state income tax rates   
21         West Virginia     WV        3  Progressive state income tax rates   
22             Wisconsin     WI        3  Progressive state income tax rates   

               TaxType_str_short fill_color  
0   Progressive income tax rates       blue  
1   Progressive income tax rates       blue  
2   Progressive income tax rates       blue  
3   Progressive income tax rates       blue  
4   Progressive income tax rates       blue  
5   Progressive income tax rates       blue  
6   Progressive income tax rates       blue  
7   Progressive income tax rates       blue  
8   Progressive income tax rates       blue  
9   Progressive income tax rates       blue  
10  Progressive income tax rates       blue  
11  Progressive income tax rates       blue  
12  Progressive income tax rates       blue  
13  Progressive income tax rates       blue  
14  Progressive income tax rates       blue  
15  Progressive income tax rates       blue  
16  Progressive income tax rates       blue  
17  Progressive income tax rates       blue  
18  Progressive income tax rates       blue  
19  Progressive income tax rates       blue  
20  Progressive income tax rates       blue  
21  Progressive income tax rates       blue  
22  Progressive income tax rates       blue

Create the Bokeh state map figure.

In [7]:
fig1_title = (
    "Figure 1. Type of state child tax credit as of January 1, 2024"
)
# fig1_title = ""
output_file(
    "./images/state_ctc_type_2024.html", title=fig1_title, mode='inline'
)
output_notebook()

# Download U.S. states shape files from US Census Bureau
# https://www.census.gov/geographies/mapping-files/2018/geo/carto-boundary-file.html
us_shapefile_path = ("https://github.com/TheCGO/ID-CTC/raw/main/data/" +
                     "cb_2018_us_state_20m/cb_2018_us_state_20m.shp")
gdf = gpd.GeoDataFrame.from_file(us_shapefile_path)
gdf_json = gdf.to_json()
gjson = json.loads(gdf_json)

# Remove Puerto Rico from data
del(gjson["features"][7])

# Alaska
# Fix positive longitudes
min_lat_ak = 180  # initial value that will be adjusted
min_abs_lon_ak = 180  # initial value that will be adjusted
coords_list = gjson["features"][24]["geometry"]["coordinates"]
for ind_isl, island in enumerate(coords_list):
    for ind_pnt, point in enumerate(island[0]):
        min_lat_ak = np.minimum(min_lat_ak, point[1])
        if point[0] > 0:
            gjson["features"][24]["geometry"][
                "coordinates"
            ][ind_isl][0][ind_pnt][0] = -180 - (180 - point[0])
        else:
            min_abs_lon_ak = np.minimum(min_abs_lon_ak, -point[0])

# Shrink the size of Alaska relative to its southestern most minimum lattitude
# and longitude
shrink_pct_ak = 0.65
coords_list_ak = gjson["features"][24]["geometry"]["coordinates"]
for ind_isl, island in enumerate(coords_list_ak):
    for ind_pnt, point in enumerate(island[0]):
        gjson["features"][24]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][0] = point[0] - shrink_pct_ak * (point[0] +
                                                                min_abs_lon_ak)
        gjson["features"][24]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][1] = point[1] - shrink_pct_ak * (point[1] -
                                                                min_lat_ak)

# Move Alaska closer to the mainland such that the minimum minimum absolute
# longitude and lattitude are (-127, 44)
min_lat_ak_new = 44
min_abs_lon_ak_new = 127
for ind_isl, island in enumerate(coords_list):
    for ind_pnt, point in enumerate(island[0]):
        gjson["features"][24]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][0] = point[0] + (min_abs_lon_ak -
                                                min_abs_lon_ak_new)
        gjson["features"][24]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][1] = point[1] - (min_lat_ak - min_lat_ak_new)

# Hawaii
list_ind_hi = 47
# Get minimum lattitude and minimum absolute longitude for Hawaii
min_lat_hi = 180  # initial value that will be adjusted
min_abs_lon_hi = 180  # initial value that will be adjusted
coords_list = gjson["features"][list_ind_hi]["geometry"]["coordinates"]
for ind_isl, island in enumerate(coords_list):
    for ind_pnt, point in enumerate(island[0]):
        min_lat_hi = np.minimum(min_lat_hi, point[1])
        min_abs_lon_hi = np.minimum(min_abs_lon_hi, -point[0])
# print("Minimum lattitude for Hawaii is", min_lat_hi)
# print("Minimum absolute longitude for Hawaii is", min_abs_lon_hi)

# Increase the size of Hawaii
incr_pct_hi = 0.4
coords_list_hi = gjson["features"][list_ind_hi]["geometry"]["coordinates"]
for ind_isl, island in enumerate(coords_list_hi):
    for ind_pnt, point in enumerate(island[0]):
        gjson["features"][list_ind_hi]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][0] = point[0] + incr_pct_hi * (point[0] +
                                                              min_abs_lon_hi)
        gjson["features"][list_ind_hi]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][1] = point[1] + incr_pct_hi * (point[1] -
                                                              min_lat_hi)

# Move Hawaii closer to the mainland such that the minimum minimum absolute
# longitude and lattitude are (-125, 27)
min_lat_hi_new = 27.5
min_abs_lon_hi_new = 124.5
for ind_isl, island in enumerate(coords_list):
    for ind_pnt, point in enumerate(island[0]):
        gjson["features"][list_ind_hi]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][0] = point[0] + (min_abs_lon_hi -
                                                min_abs_lon_hi_new)
        gjson["features"][list_ind_hi]["geometry"][
            "coordinates"
        ][ind_isl][0][ind_pnt][1] = point[1] - (min_lat_hi - min_lat_hi_new)

# Add a state box around Delaware abbreviation DE
st_list_num = 2
de_coord_list = [gjson["features"][st_list_num]["geometry"]["coordinates"]]
new_box_de = [[
    [-75.4, 38.8],
    [-72.4, 38.3],
    [-72.4, 38.9],
    [-70.2, 38.9],
    [-70.2, 37.7],
    [-72.4, 37.7],
    [-72.4, 38.3]
]]
de_coord_list.append(new_box_de)
gjson["features"][st_list_num]["geometry"]["coordinates"] = de_coord_list
gjson["features"][st_list_num]["geometry"]["type"] = "MultiPolygon"

# Add a state box around Washington, DC (District of Columbia) abbreviation DC
st_list_num = 35
dc_coord_list = [gjson["features"][st_list_num]["geometry"]["coordinates"]]
new_box_dc = [[
    [-77.0, 38.9],
    [-73.3, 35.5],
    [-73.3, 36.1],
    [-71.1, 36.1],
    [-71.1, 34.9],
    [-73.3, 34.9],
    [-73.3, 35.5]
]]
dc_coord_list.append(new_box_dc)
gjson["features"][st_list_num]["geometry"]["coordinates"] = dc_coord_list
gjson["features"][st_list_num]["geometry"]["type"] = "MultiPolygon"

# Add a state box around Massachusetts abbreviation MD
st_list_num = 0
md_coord_list = gjson["features"][st_list_num]["geometry"]["coordinates"]
new_box_md = [[
    [-76.8, 39.3],
    [-72.7, 37.0],
    [-72.7, 37.6],
    [-70.5, 37.6],
    [-70.5, 36.4],
    [-72.7, 36.4],
    [-72.7, 37.0]
]]
md_coord_list.append(new_box_md)
gjson["features"][st_list_num]["geometry"]["coordinates"] = md_coord_list

# Add a state box around Massachusetts abbreviation MA
st_list_num = 29
ma_coord_list = gjson["features"][st_list_num]["geometry"]["coordinates"]
new_box_ma = [[
    [-71.7, 42.2],
    [-68.5, 42.2],
    [-68.5, 42.8],
    [-66.3, 42.8],
    [-66.3, 41.6],
    [-68.5, 41.6],
    [-68.5, 42.2]
]]
ma_coord_list.append(new_box_ma)
gjson["features"][st_list_num]["geometry"]["coordinates"] = ma_coord_list

# Add a state box around New Jersey abbreviation NJ
st_list_num = 34
nj_coord_list = [gjson["features"][st_list_num]["geometry"]["coordinates"]]
new_box_nj = [[
    [-74.4, 40.1],
    [-72.0, 39.7],
    [-72.0, 40.3],
    [-69.8, 40.3],
    [-69.8, 39.1],
    [-72.0, 39.1],
    [-72.0, 39.7]
]]
nj_coord_list.append(new_box_nj)
gjson["features"][st_list_num]["geometry"]["coordinates"] = nj_coord_list
gjson["features"][st_list_num]["geometry"]["type"] = "MultiPolygon"

# Add a state box around Rhode Island abbreviation RI
st_list_num = 50
ri_coord_list = gjson["features"][st_list_num]["geometry"]["coordinates"]
new_box_ri = [[
    [-71.5, 41.7],
    [-69.5, 40.4],
    [-69.5, 41.0],
    [-67.3, 41.0],
    [-67.3, 39.8],
    [-69.5, 39.8],
    [-69.5, 40.4]
]]
ri_coord_list.append(new_box_ri)
gjson["features"][st_list_num]["geometry"]["coordinates"] = ri_coord_list

# Merge the state tax type data into gjson for each state
state_taxtype_df
for ind_st, state in enumerate(gjson["features"]):
    st_abbrev = state["properties"]["STUSPS"]
    state["properties"]["tax_type"] = state_taxtype_df[
        state_taxtype_df["Abbrev"]==st_abbrev
    ]["TaxType_str_short"].iloc[0]

tax_type_labels = [
    'No income tax', 'Flat income tax rate', 'Nearly flat income tax rates',
    'Progressive income tax rates'
]
tax_type_colors = ["white", "red", "purple", "blue"]

source_shapes = {}
for category in tax_type_labels:
    source_shapes[category] = {"type": "FeatureCollection", "features": []}

for item in gjson["features"]:
    source_shapes[item["properties"]["tax_type"]]['features'].append(item)

TOOLS = "pan, box_zoom, wheel_zoom, hover, save, reset, help"

fig1 = figure(
    title=fig1_title,
    height=500,
    width=1050,
    tools=TOOLS,
    # tooltips=[
    #     ("State", @state_names), ("Tax type", @tax_type)
    # ]
    # match_aspect = True,
    min_border = 0,
    x_axis_location = None, y_axis_location = None,
    toolbar_location="right"
)
fig1.title.text_font_size = "15pt"
fig1.toolbar.logo = None
fig1.grid.grid_line_color = None

cmap = CategoricalColorMapper(
    palette=tax_type_colors, factors=tax_type_labels
)
for category in tax_type_labels:
    source_shape_1 = GeoJSONDataSource(
        geojson = json.dumps(source_shapes[category])
    )
    fig1.patches(
        'xs', 'ys', source=source_shape_1, fill_alpha=0.7,
        fill_color = {'field': 'tax_type', 'transform': cmap},
        line_color ='black', line_width=1.0, line_alpha=0.3,
        hover_line_color="black", hover_line_width=3.0, legend_label=category)

    hover = fig1.select_one(HoverTool)
    hover.point_policy = "follow_mouse"
    hover.tooltips = [
        ("State", "@NAME"),
        ("Tax type", "@tax_type")
    ]

# Add 2-letter state abbreviation labels. See Bokeh documentation for labels at
# https://docs.bokeh.org/en/latest/docs/user_guide/basic/annotations.html.
label_lon_lat =[
    ["AL",  -87.40, 32.10],
    ["AK", -135.00, 48.30],
    ["AZ", -112.40, 34.00],
    ["AR",  -93.20, 34.30],
    ["CA", -121.00, 37.00],
    ["CO", -106.50, 38.50],
    ["CT",  -73.40, 41.15],
    ["DE",  -72.10, 37.80],
    ["DC",  -73.00, 35.00],
    ["FL",  -82.40, 28.00],
    ["GA",  -84.20, 32.20],
    ["HI", -125.00, 29.00],
    ["ID", -115.00, 43.00],
    ["IL",  -89.60, 39.50],
    ["IN",  -86.90, 39.60],
    ["IA",  -94.40, 41.60],
    ["KS",  -99.50, 38.00],
    ["KY",  -86.00, 37.00],
    ["LA",  -93.00, 30.20],
    ["ME",  -70.00, 44.50],
    ["MD",  -72.40, 36.50],
    ["MA",  -68.20, 41.80],
    ["MI",  -85.40, 42.70],
    ["MN",  -95.30, 45.50],
    ["MS",  -90.60, 32.10],
    ["MO",  -93.50, 38.00],
    ["MT", -110.50, 46.50],
    ["NE", -100.50, 41.00],
    ["NV", -118.00, 39.00],
    ["NH",  -72.45, 42.70],
    ["NM", -107.00, 34.00],
    ["NJ",  -71.60, 39.20],
    ["NY",  -76.00, 42.50],
    ["NC",  -79.20, 35.00],
    ["ND", -101.50, 46.80],
    ["OH",  -83.80, 39.90],
    ["OK",  -98.00, 35.00],
    ["OR", -121.50, 43.50],
    ["PA",  -78.50, 40.40],
    ["RI",  -69.00, 39.90],
    ["SC",  -81.50, 33.30],
    ["SD", -101.00, 44.00],
    ["TN",  -87.10, 35.40],
    ["TX", -100.00, 31.00],
    ["UT", -112.50, 39.00],
    ["VT",  -73.20, 44.10],
    ["VA",  -79.00, 37.10],
    ["WA", -121.00, 47.00],
    ["WV",  -81.90, 38.00],
    ["WI",  -90.40, 44.00],
    ["WY", -108.50, 42.50]
]
label_abbrev = [state[0] for state in label_lon_lat]
label_lon = [state[1] for state in label_lon_lat]
label_lat = [state[2] for state in label_lon_lat]
state_cds = ColumnDataSource(data=dict(
    lon=label_lon,
    lat=label_lat,
    abbrev=label_abbrev
))

state_labels = LabelSet(
    x='lon', y='lat', text='abbrev', text_font_size="9pt",
    text_font_style="bold", x_offset=0, y_offset=0, source=state_cds
)

fig1.add_layout(state_labels)

# Legend properties
fig1.legend.click_policy = 'mute'
fig1.legend.location = "center_left"

fig1.add_layout(
    Title(
        text="  Source: Richard W. Evans (@RickEcon), updated March 30, 2024.",
        align="left",
        text_font_size="3mm",
        text_font_style="italic",
    ),
    "below"
)
show(fig1)

Loading BokehJS ...

## 2. Idaho Child Tax Credit

## 3. Effects of increasing the ID CTC on Idaho tax filers

### 3.1. Define the 18 filer types: Married and Head of Household; 1, 2, and 3 children; low, medium, and high income

#### 3.1.1. Define the nine Married Filing Jointly filer types: 1, 2, and 3 children; low, middle, and high income

Married filing jointly, 1 kid, low income (household before-tax income = $25,000)

In [8]:
situation_mar_1_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "25000"},
            "medical_out_of_pocket_expenses": {"2024": "450"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "0"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "600"},
            "housing_cost": {"2024": "10000"},
            "phone_cost": {"2024": "800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Married filing jointly, 1 kid, middle income (household before-tax income = $70,000)

In [9]:
situation_mar_1_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "employment_income": {"2024": "40000"},
            "medical_out_of_pocket_expenses": {"2024": "1850"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "30000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "1300"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Married filing jointly, 1 kid, high income (household before-tax income = $200,000)

In [10]:
situation_mar_1_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "20000"},
            "employment_income": {"2024": "100000"},
            "medical_out_of_pocket_expenses": {"2024": "2450"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "100000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "1700"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Married filing jointly, 2 kids, low income (household before-tax income = $25,000)

In [11]:
situation_mar_2_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "25000"},
            "medical_out_of_pocket_expenses": {"2024": "600"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "0"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "1000"},
            "housing_cost": {"2024": "10000"},
            "phone_cost": {"2024": "800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Married filing jointly, 2 kids, middle income (household before-tax income = $70,000)

In [12]:
situation_mar_2_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "employment_income": {"2024": "40000"},
            "medical_out_of_pocket_expenses": {"2024": "2500"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "30000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "2200"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Married filing jointly, 2 kids, high income (household before-tax income = $200,000)

In [13]:
situation_mar_2_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "20000"},
            "employment_income": {"2024": "100000"},
            "medical_out_of_pocket_expenses": {"2024": "3500"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "100000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "3000"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Married filing jointly, 3 kids, low income (household before-tax income = $25,000)

In [14]:
situation_mar_3_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "25000"},
            "medical_out_of_pocket_expenses": {"2024": "900"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "0"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "1400"},
            "housing_cost": {"2024": "10000"},
            "phone_cost": {"2024": "800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

 Married filing jointly, 3 kids, middle income (household before-tax income = $70,000)

In [15]:
situation_mar_3_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "employment_income": {"2024": "40000"},
            "medical_out_of_pocket_expenses": {"2024": "3600"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "30000"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "3100"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Married filing jointly, 3 kids, high income (household before-tax income = $200,000)

In [16]:
situation_mar_3_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "20000"},
            "employment_income": {"2024": "100000"},
            "medical_out_of_pocket_expenses": {"2024": "4900"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "100000"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "4400"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

#### 3.1.2. Define the nine Head of Household filer types: 1, 2, and 3 children; low, middle, and high income

Head of household, 1 kid, low income (household before-tax income = $20,000)

In [17]:
situation_hoh_1_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "20000"},
            "medical_out_of_pocket_expenses": {"2024": "400"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "600"},
            "housing_cost": {"2024": "7000"},
            "phone_cost": {"2024": "600"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 1 kid, middle income (household before-tax income = $60,000)

In [18]:
situation_hoh_1_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "employment_income": {"2024": "60000"},
            "medical_out_of_pocket_expenses": {"2024": "1500"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "1100"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 1 kid, high income (household before-tax income = $150,000)

In [19]:
situation_hoh_1_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "15000"},
            "employment_income": {"2024": "150000"},
            "medical_out_of_pocket_expenses": {"2024": "2200"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "1800"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 2 kids, low income (household before-tax income = $20,000)

In [20]:
situation_hoh_2_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "20000"},
            "medical_out_of_pocket_expenses": {"2024": "500"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "1000"},
            "housing_cost": {"2024": "9000"},
            "phone_cost": {"2024": "600"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 2 kids, middle income (household before-tax income = $60,000)

In [21]:
situation_hoh_2_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "employment_income": {"2024": "60000"},
            "medical_out_of_pocket_expenses": {"2024": "2000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "2000"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 2 kids, high income (household before-tax income = $150,000)

In [22]:
situation_hoh_2_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "15000"},
            "employment_income": {"2024": "150000"},
            "medical_out_of_pocket_expenses": {"2024": "3000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "3000"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 3 kids, low income (household before-tax income = $20,000)

In [27]:
situation_hoh_3_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "20000"},
            "medical_out_of_pocket_expenses": {"2024": "700"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "1400"},
            "housing_cost": {"2024": "9000"},
            "phone_cost": {"2024": "600"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 3 kids, middle income (household before-tax income = $60,000)

In [24]:
situation_hoh_3_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "employment_income": {"2024": "60000"},
            "medical_out_of_pocket_expenses": {"2024": "2900"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "2900"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

Head of household, 3 kids, high income (household before-tax income = $150,000)

In [25]:
situation_hoh_3_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "15000"},
            "employment_income": {"2024": "150000"},
            "medical_out_of_pocket_expenses": {"2024": "4300"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "4300"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    }
}

### 3.2. Analyses for the ID Child Tax Credit increase

#### 3.2.1. Run all baseline and reform simulations for the ID Child Tax Credit increase

In [28]:
# Create baseline (no change) parameters
def modify_parameters_b(parameters):
    """
    Baseline reform is to not modify the parameters.
    """
    pass
    return parameters


# Create  baseline (no change) reform
class reform_b(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters_b)


# Define the parameters that change in the reform
def modify_parameters_1(parameters):
    # Increase the ID CTC from $205 to $250
    parameters.gov.states.id.tax.income.credits.ctc.amount.update(
        start=instant("2024-01-01"), stop=instant("2024-12-31"),
        value=250)

    return parameters


class reform_1(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters_1)


def calculate_base_reform(sim_name, base_reform, reform, situation):
    print("Simulating baseline scenario for:", sim_name)
    simulation_b = Simulation(reform=base_reform, situation=situation)
    # simulation_b.trace = True
    income_before_tax = sum(simulation_b.calculate("employment_income", 2024))
    income_after_tax_b = simulation_b.calculate("household_net_income", 2024)[0]
    id_net_tax_liability_b = simulation_b.calculate("id_income_tax", 2024)[0]
    print("Simulating reform scenario for:", sim_name)
    simulation_r = Simulation(reform=reform, situation=situation)
    # simulation_r.trace = True
    income_after_tax_r = simulation_r.calculate("household_net_income", 2024)[0]
    id_net_tax_liability_r = simulation_r.calculate("id_income_tax", 2024)[0]
    id_net_tax_liab_dol_chg = id_net_tax_liability_r - id_net_tax_liability_b
    id_net_tax_liab_pct_chg = (id_net_tax_liab_dol_chg /
                               np.absolute(id_net_tax_liability_b))
    print("")
    return (
        income_before_tax, income_after_tax_b, id_net_tax_liability_b,
        income_after_tax_r, id_net_tax_liability_r, id_net_tax_liab_dol_chg,
        id_net_tax_liab_pct_chg
    )

simulations = [
    ('Head of household, 1 kid, low income', situation_hoh_1_low),
    ('Head of household, 1 kid, middle income', situation_hoh_1_mid),
    ('Head of household, 1 kid, high income', situation_hoh_1_high),
    ('Head of household, 2 kids, low income', situation_hoh_2_low),
    ('Head of household, 2 kids, middle income', situation_hoh_2_mid),
    ('Head of household, 2 kids, high income', situation_hoh_2_high),
    ('Head of household, 3 kids, low income', situation_hoh_3_low),
    ('Head of household, 3 kids, middle income', situation_hoh_3_mid),
    ('Head of household, 3 kids, high income', situation_hoh_3_high),
    ('Married, 1 kid, low income', situation_mar_1_low),
    ('Married, 1 kid, middle income', situation_mar_1_mid),
    ('Married, 1 kid, high income', situation_mar_1_high),
    ('Married, 2 kids, low income', situation_mar_2_low),
    ('Married, 2 kids, middle income', situation_mar_2_mid),
    ('Married, 2 kids, high income', situation_mar_2_high),
    ('Married, 3 kids, low income', situation_mar_3_low),
    ('Married, 3 kids, middle income', situation_mar_3_mid),
    ('Married, 3 kids, high income', situation_mar_3_high),
]

results = []

# Loop through each simulation
for sim_name, situation in simulations:
    # Calculate before_tax_income, after_tax_income, and id_net_tax_liability
    (income_before_tax, income_after_tax_b, id_net_tax_liability_b,
     income_after_tax_r, id_net_tax_liability_r, id_net_tax_liab_dol_chg,
     id_net_tax_liab_pct_chg) = calculate_base_reform(sim_name, reform_b,
                                                      reform_1, situation)

    # Append the results as a dictionary where key is the column name and value
    # is the simulation output
    results.append({
        "Situation": sim_name,
        "Before tax income": income_before_tax,
        "Baseline after tax income": income_after_tax_b,
        "Baseline Idaho net tax liability": id_net_tax_liability_b,
        "Reform after tax income": income_after_tax_r,
        "Reform Idaho net tax liability": id_net_tax_liability_r,
        "Idaho net tax liability change, dollars": id_net_tax_liab_dol_chg,
        "Idaho net tax liability change, percent": id_net_tax_liab_pct_chg
    })

# Convert the results to a DataFrame
df = pd.DataFrame(results)

# Check the DataFrame
df

Simulating baseline scenario for: Head of household, 1 kid, low income
Simulating reform scenario for: Head of household, 1 kid, low income

Simulating baseline scenario for: Head of household, 1 kid, middle income
Simulating reform scenario for: Head of household, 1 kid, middle income

Simulating baseline scenario for: Head of household, 1 kid, high income
Simulating reform scenario for: Head of household, 1 kid, high income

Simulating baseline scenario for: Head of household, 2 kids, low income
Simulating reform scenario for: Head of household, 2 kids, low income

Simulating baseline scenario for: Head of household, 2 kids, middle income
Simulating reform scenario for: Head of household, 2 kids, middle income

Simulating baseline scenario for: Head of household, 2 kids, high income
Simulating reform scenario for: Head of household, 2 kids, high income

Simulating baseline scenario for: Head of household, 3 kids, low income
Simulating reform scenario for: Head of household, 3 kids, l

Situation  Before tax income  \
0       Head of household, 1 kid, low income            20000.0   
1    Head of household, 1 kid, middle income            60000.0   
2      Head of household, 1 kid, high income           150000.0   
3      Head of household, 2 kids, low income            20000.0   
4   Head of household, 2 kids, middle income            60000.0   
5     Head of household, 2 kids, high income           150000.0   
6      Head of household, 3 kids, low income            20000.0   
7   Head of household, 3 kids, middle income            60000.0   
8     Head of household, 3 kids, high income           150000.0   
9                 Married, 1 kid, low income            25000.0   
10             Married, 1 kid, middle income            70000.0   
11               Married, 1 kid, high income           200000.0   
12               Married, 2 kids, low income            25000.0   
13            Married, 2 kids, middle income            70000.0   
14              Married, 2 kids, high income           200000.0   
15               Married, 3 kids, low income            25000.0   
16            Married, 3 kids, middle income            70000.0   
17              Married, 3 kids, high income           200000.0   

    Baseline after tax income  Baseline Idaho net tax liability  \
0                31007.599609                       -445.000000   
1                53389.000000                       1039.017944   
2               118792.000000                       6259.018066   
3                39190.398438                       -770.000000   
4                55569.000000                        509.017944   
5               121032.000000                       5729.018066   
6                43736.000000                      -1095.000000   
7                58109.000000                        -20.982056   
8               123292.000000                       5199.018066   
9                37497.101562                       -565.000000   
10               62473.000000                       1075.618042   
11              159358.000000                       8615.618164   
12               45594.699219                       -890.000000   
13               64653.000000                        545.618042   
14              161618.000000                       8085.618164   
15               49980.703125                      -1215.000000   
16               67193.000000                         15.618042   
17              163898.000000                       7555.618164   

    Reform after tax income  Reform Idaho net tax liability  \
0              31007.599609                     -490.000000   
1              53389.000000                      949.017944   
2             118792.000000                     6169.018066   
3              39190.398438                     -860.000000   
4              55569.000000                      329.017944   
5             121032.000000                     5549.018066   
6              43736.000000                    -1230.000000   
7              58109.000000                     -290.982056   
8             123292.000000                     4929.018066   
9              37497.101562                     -610.000000   
10             62473.000000                      985.618042   
11            159358.000000                     8525.618164   
12             45594.699219                     -980.000000   
13             64653.000000                      365.618042   
14            161618.000000                     7905.618164   
15             49980.703125                    -1350.000000   
16             67193.000000                     -254.381958   
17            163898.000000                     7285.618164   

    Idaho net tax liability change, dollars  \
0                                     -45.0   
1                                     -90.0   
2                                     -90.0   
3                                     -90.0   
4                                    -180.0   
5      

#### 3.2.2 Make plot of Idaho net tax liability by before-tax income for 6 filer types: Married or Head of Household; 1, 2, or 3 kids

##### 3.2.2.1. Create the four new filers with employment income allowed to vary

In [29]:
inc_min = 0
inc_max = 200_000
num_points = 10001

Create new Married Filing Jointly filer with one child, the same other characteristics as the middle income type, and income varying.

In [30]:
situation_mar_1_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "medical_out_of_pocket_expenses": {"2024": "1850"},
        },
        "your partner": {
            "age": {"2024": "35"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "1300"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}

Create new Married Filing Jointly filer with two children, the same other characteristics as the middle income type, and income varying.

In [31]:
situation_mar_2_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "medical_out_of_pocket_expenses": {"2024": "2500"},
        },
        "your partner": {
            "age": {"2024": "35"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "2200"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}

Create new Married Filing Jointly filer with three children, the same other characteristics as the middle income type, and income varying.

In [32]:
situation_mar_3_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "medical_out_of_pocket_expenses": {"2024": "3600"},
        },
        "your partner": {
            "age": {"2024": "35"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "3100"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}

Create new Head of Household filer with one child, the same other characteristics as the middle income type, and income varying.

In [33]:
situation_hoh_1_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "medical_out_of_pocket_expenses": {"2024": "1500"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "1100"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}

Create new Head of Household filer with two children, the same other characteristics as the middle income type, and income varying.

In [34]:
situation_hoh_2_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "medical_out_of_pocket_expenses": {"2024": "2000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "2000"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}

Create new Head of Household filer with three children, the same other characteristics as the middle income type, and income varying.

In [35]:
situation_hoh_3_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "medical_out_of_pocket_expenses": {"2024": "2900"},
        },
        "your first dependent": {
            "age": {"2024": "13"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your third dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        },
        "your third dependent's marital unit": {
            "members": ["your third dependent"],
            "marital_unit_id": {"2024": 4}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "2900"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent",
                "your third dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "ID"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}

##### 3.2.2.2. Create the plot of the six filer types varying by income

Create the data series for the four lines of the plot.

In [40]:
def calculate_base_reform_plot(sim_name, base_reform, reform, situation):
    print("Simulating baseline scenario for plot:", sim_name)
    simulation_b = Simulation(reform=base_reform, situation=situation)
    simulation_b.trace = True
    income_before_tax_vec = simulation_b.calculate("employment_income", 2024)
    income_after_tax_b_vec = simulation_b.calculate("household_net_income",
                                                    2024)
    id_net_tax_liability_b_vec = simulation_b.calculate("id_income_tax", 2024)
    print("Simulating reform scenario for plot:", sim_name)
    simulation_r = Simulation(reform=reform, situation=situation)
    simulation_r.trace = True
    income_after_tax_r_vec = simulation_r.calculate("household_net_income",
                                                    2024)
    id_net_tax_liability_r_vec = simulation_r.calculate("id_income_tax", 2024)
    id_net_tax_liab_dol_chg_vec = (id_net_tax_liability_r_vec -
                                   id_net_tax_liability_b_vec)
    id_net_tax_liab_pct_chg_vec = (id_net_tax_liab_dol_chg_vec /
                                   np.absolute(id_net_tax_liability_b_vec))
    print("")
    return (
        income_before_tax_vec, income_after_tax_b_vec,
        id_net_tax_liability_b_vec, income_after_tax_r_vec,
        id_net_tax_liability_r_vec, id_net_tax_liab_dol_chg_vec,
        id_net_tax_liab_pct_chg_vec
    )

results_plot = []
df_list = []
cds_list = []
filer_type_label_list = []

sims_to_plot = [
    ('Married filing jointly, 1 kid', situation_mar_1_mid_plot),
    ('Married filing jointly, 2 kids', situation_mar_2_mid_plot),
    ('Married filing jointly, 3 kids', situation_mar_3_mid_plot),
    ('Head of household, 1 kid', situation_hoh_1_mid_plot),
    ('Head of household, 2 kids', situation_hoh_2_mid_plot),
    ('Head of household, 3 kids', situation_hoh_3_mid_plot)
]

# Loop through each simulation with varying income
for sim_name, situation in sims_to_plot:
    # Calculate before_tax_income, after_tax_income, and id_net_tax_liability
    (inc_before_tax_vec, inc_after_tax_b_vec, id_net_tax_liab_b_vec,
     inc_after_tax_r_vec, id_net_tax_liab_r_vec,
     id_net_tax_liab_dol_chg_vec, id_net_tax_liab_pct_chg_vec) = \
        calculate_base_reform_plot(sim_name, reform_b, reform_1, situation)
    # Create a DataFrame
    data_df = pd.DataFrame([])
    if sim_name == "Head of household, 1 kid":
        # Income before tax array gives incomes for head of household and
        # child. Take only every second index 0, 2, 4,... .
        data_df["inc_before_tax"] = inc_before_tax_vec[0::2]
    elif (
        (sim_name == "Married filing jointly, 1 kid") or
        (sim_name == "Head of household, 2 kids")
    ):
        # Income before tax array gives incomes for both spouses and one child
        # for Married filing jointly, 1 kid; and give for head of
        # household and for both children. Take only every third
        # index 0, 3, 6,... .
        data_df["inc_before_tax"] = inc_before_tax_vec[0::3]
    elif (
        (sim_name == "Married filing jointly, 2 kids") or
        (sim_name == "Head of household, 3 kids")
    ):
        # Income before tax array gives incomes for both spouses and for both
        # children for Married filing jointly, 2 kids; and give for head of
        # household and for all three children. Take only every fourth
        # index 0, 4, 8,... .
        data_df["inc_before_tax"] = inc_before_tax_vec[0::4]
    elif sim_name == "Married filing jointly, 3 kids":
        # Income before tax array gives incomes for both spouses and for all
        # three children for Married filing jointly, 3 kids. Take only every
        # fifth index 0, 5, 10,... .
        data_df["inc_before_tax"] = inc_before_tax_vec[0::5]

    data_df["inc_after_tax_b"] = inc_after_tax_b_vec
    data_df["id_net_tax_liab_b"] = id_net_tax_liab_b_vec
    data_df["inc_after_tax_r"] = inc_after_tax_r_vec
    data_df["id_net_tax_liab_r"] = id_net_tax_liab_r_vec
    data_df["id_net_tax_liab_dol_chg"] = id_net_tax_liab_dol_chg_vec
    data_df["id_net_tax_liab_pct_chg"] = id_net_tax_liab_pct_chg_vec
    data_df["filer_type"] = sim_name

    # Append the sim name to the filer_type_label_list
    filer_type_label_list.append(sim_name)

    # Append the results as a dictionary where key is the column name and value
    # is the simulation output
    results_plot.append({
        "Situation": sim_name,
        "Before tax income vector": inc_before_tax_vec,
        "Baseline Idaho net tax liability vector": id_net_tax_liab_b_vec,
        "Reform Idaho net tax liability vector": id_net_tax_liab_r_vec,
        "Idaho net tax liability change vector, dollars": id_net_tax_liab_dol_chg_vec,
        "Pandas DataFrame": data_df
    })

    # Append the data_df as a Pandas DataFrame object to the df_list
    df_list.append(data_df)

    # Append the data_df as a ColumnDataSource object to the cds_list
    cds_list.append(ColumnDataSource(data_df))


Simulating baseline scenario for plot: Married filing jointly, 1 kid
Simulating reform scenario for plot: Married filing jointly, 1 kid

Simulating baseline scenario for plot: Married filing jointly, 2 kids
Simulating reform scenario for plot: Married filing jointly, 2 kids

Simulating baseline scenario for plot: Married filing jointly, 3 kids
Simulating reform scenario for plot: Married filing jointly, 3 kids

Simulating baseline scenario for plot: Head of household, 1 kid
Simulating reform scenario for plot: Head of household, 1 kid

Simulating baseline scenario for plot: Head of household, 2 kids
Simulating reform scenario for plot: Head of household, 2 kids

Simulating baseline scenario for plot: Head of household, 3 kids
Simulating reform scenario for plot: Head of household, 3 kids



In [41]:
# Save source data for figure 2
fig2_source_df = df_list[0][["inc_before_tax", "id_net_tax_liab_dol_chg"]].rename(columns={"id_net_tax_liab_dol_chg": "id_net_tax_liab_dol_chg_single"})
fig2_source_df["id_net_tax_liab_dol_chg_mar0kids"] = df_list[1]["id_net_tax_liab_dol_chg"]
fig2_source_df["id_net_tax_liab_dol_chg_hoh2kids"] = df_list[2]["id_net_tax_liab_dol_chg"]
fig2_source_df["id_net_tax_liab_dol_chg_mar2kids"] = df_list[3]["id_net_tax_liab_dol_chg"]
fig2_source_df.to_csv('./data/fig2_source.csv', index=False)

Create the Bokeh plot for Figure 2.

In [46]:
# Create Bokeh plot of Figure 2 change in Idaho net tax liability for an
# increase in the ID CTC
fig2_title = (
    "Fig. 2. Dollar change from increase in ID CTC in filer net state " +
    "income tax liability"
)
# fig2_title = ""
filename2 = "./images/NetStateTaxLiabChg_ref1.html"
output_file(filename2, title=fig2_title, mode='inline')
output_notebook()

# Format the tooltip
tooltips = [
    ("Filer type", "@filer_type"),
    ("Before-tax employment income", "$x{$0,0.}"),
    ("Change in Idaho net tax liability", "$y{$0,0.}"),
]

# Solve for minimum and maximum before-tax income and change in tax liability
# values in order to set the appropriate xrange and yrange
min_xval = inc_min
max_xval = inc_max
datarange_xvals = inc_max - inc_min
min_yval = 1e10
max_yval = -1e10
for filer_type in results_plot:
    min_yval = np.minimum(
        min_yval, filer_type[
            "Idaho net tax liability change vector, dollars"
        ].min()
    )
    max_yval = np.maximum(
        max_yval, filer_type[
            "Idaho net tax liability change vector, dollars"
        ].max()
    )
datarange_yvals = max_yval - min_yval
fig2_buffer_pct = 0.05
fig2 = figure(
    height=500,
    width=800,
    x_axis_label="Before-tax employment income",
    y_axis_label="Change in Idaho net tax liability",
    y_range=(
        -300,  # min_yval,
        25  # max_yval + fig2_buffer_pct * datarange_yvals
    ),
    x_range=(
        15_000,  # min_xval,
        75_000  # max_xval
    ),
    tools=[
        "save",
        "zoom_in",
        "zoom_out",
        "box_zoom",
        "pan",
        "undo",
        "redo",
        "reset",
        "hover",
        "help",
    ],
    toolbar_location="right",
)
fig2.toolbar.logo = None

l0 = fig2.line(
    x="inc_before_tax",
    y="id_net_tax_liab_dol_chg",
    source=cds_list[0],
    # color="blue",
    color=Category10[6][0],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l1 = fig2.line(
    x="inc_before_tax",
    y="id_net_tax_liab_dol_chg",
    source=cds_list[1],
    # color="purple", 
    color=Category10[6][1],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l2 = fig2.line(
    x="inc_before_tax",
    y="id_net_tax_liab_dol_chg",
    source=cds_list[2],
    # color="green",
    color=Category10[6][2],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l3 = fig2.line(
    x="inc_before_tax",
    y="id_net_tax_liab_dol_chg",
    source=cds_list[3],
    # color="red",
    color=Category10[6][3],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l4 = fig2.line(
    x="inc_before_tax",
    y="id_net_tax_liab_dol_chg",
    source=cds_list[4],
    # color="green",
    color=Category10[6][4],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l5 = fig2.line(
    x="inc_before_tax",
    y="id_net_tax_liab_dol_chg",
    source=cds_list[5],
    # color="red",
    color=Category10[6][5],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)

# Dashed horizontal line at $0 change
fig2.line(
    x=[min_xval - fig2_buffer_pct * datarange_xvals,
       max_xval + fig2_buffer_pct * datarange_xvals],
    y=[0.0, 0.0],
    color="black",
    line_width=2,
    line_dash="dashed",
    alpha=0.5,
)

# Add title
fig2.add_layout(
    Title(
        text=fig2_title,
        text_font_style="bold",
        text_font_size="14pt",
        align="center",
    ),
    "above",
)

# Add legend
legend = Legend(
    items=[
        (filer_type_label_list[0], [l0]),
        (filer_type_label_list[1], [l1]),
        (filer_type_label_list[2], [l2]),
        (filer_type_label_list[3], [l3]),
        (filer_type_label_list[4], [l4]),
        (filer_type_label_list[5], [l5]),
    ],
    # location="center",
)
fig2.add_layout(legend)
fig2.legend.location = "top_right"
fig2.legend.click_policy = "mute"

# Add the HoverTool to the figure
fig2.add_tools(
    HoverTool(
        tooltips=tooltips,
        toggleable=False,
    )
)

# Customize the x-axis and y-axis ticks and tick lables and gridlines
fig2.xaxis.ticker = [10_000, 20_000, 30_000, 40_000, 50_000, 60_000, 70_000,
                     80_000]
fig2.xaxis.major_label_overrides = {
    10_0000: '$10k', 20_000: '$20k', 30_000: '$30k', 40_000: '$40k',
    50_000: '$50k', 60_000: '$60k', 70_000: '$70k', 80_000: '$80k'
}
fig2.yaxis.ticker = [-300, -250, -200, -150, -100, -50, 0]
fig2.yaxis.major_label_overrides = {
    -300: '-$300', -250: '-$250', -200: '-$200', -150: '-$150', -100: '-$100',
    -50: '-$50', 0: '$0'
}

# Add source text below figure
fig2.add_layout(
    Title(
        # text="Source: Richard W. Evans (@RickEcon), FiscalSim open source " +
        # "microsimulation model of federal and state individual tax and " +
        # "benefit policy.",
        text="Source: FiscalSim-US open source " +
        "microsimulation model of federal and state individual tax and " +
        "benefit policy.",
        align="left",
        text_font_size="3mm",
        text_font_style="italic",
    ),
    "below",
)

show(fig2)


Loading BokehJS ...

### 3.3. Analyses for making the ID Child Tax Credit refundable

Define the structural reform of making the CTC refundable

Create the data series for the four lines of the plot.

In [48]:
simulation_b_low = Simulation(reform=reform_b, situation=situation_mar_1_low)
simulation_b_low.trace = True
net_inc_b_low = simulation_b_low.calculate("household_net_income", 2024)
id_net_tax_b_low = simulation_b_low.calculate("id_income_tax", 2024)
print("Household net income (baseline, low income):", net_inc_b_low)
print("Idaho net tax liability (baseline, low income):", id_net_tax_b_low)
print("")
simulation_b_low.tracer.print_computation_log()

Household net income (baseline, low income): [37497.1]
Idaho net tax liability (baseline, low income): [-565.]

  household_net_income<2024, (default)> = [37497.1]
    household_market_income<2024, (default)> = [25000.]
      employment_income<2024, (default)> = [25000.     0.     0.]
        employment_income_before_lsr<2024, (default)> = [25000.     0.     0.]
        employment_income_behavioral_response<2024, (default)> = [0. 0. 0.]
      self_employment_income<2024, (default)> = [0. 0. 0.]
      pension_income<2024, (default)> = [0. 0. 0.]
        tax_exempt_pension_income<2024, (default)> = [0. 0. 0.]
          tax_exempt_public_pension_income<2024, (default)> = [0. 0. 0.]
          tax_exempt_private_pension_income<2024, (default)> = [0. 0. 0.]
        taxable_pension_income<2024, (default)> = [0. 0. 0.]
          taxable_public_pension_income<2024, (default)> = [0. 0. 0.]
          taxable_private_pension_income<2024, (default)> = [0. 0. 0.]
      dividend_income<2024, (default

In [49]:
simulation_r1_low = Simulation(reform=reform_1, situation=situation_mar_1_low)
simulation_r1_low.trace = True
net_inc_r1_low = simulation_r1_low.calculate("household_net_income", 2024)
id_net_tax_r1_low = simulation_r1_low.calculate("id_income_tax", 2024)
print("Household net income (reform 1, low income):", net_inc_r1_low)
print("Idaho net tax liability (reform 1, low income):", id_net_tax_r1_low)
print("")
simulation_r1_low.tracer.print_computation_log()

Household net income (reform 1, low income): [37497.1]
Idaho net tax liability (reform 1, low income): [-610.]

  household_net_income<2024, (default)> = [37497.1]
    household_market_income<2024, (default)> = [25000.]
      employment_income<2024, (default)> = [25000.     0.     0.]
        employment_income_before_lsr<2024, (default)> = [25000.     0.     0.]
        employment_income_behavioral_response<2024, (default)> = [0. 0. 0.]
      self_employment_income<2024, (default)> = [0. 0. 0.]
      pension_income<2024, (default)> = [0. 0. 0.]
        tax_exempt_pension_income<2024, (default)> = [0. 0. 0.]
          tax_exempt_public_pension_income<2024, (default)> = [0. 0. 0.]
          tax_exempt_private_pension_income<2024, (default)> = [0. 0. 0.]
        taxable_pension_income<2024, (default)> = [0. 0. 0.]
          taxable_public_pension_income<2024, (default)> = [0. 0. 0.]
          taxable_private_pension_income<2024, (default)> = [0. 0. 0.]
      dividend_income<2024, (default